In [ ]:
spark = %adb_spark add \
    --spark-conf spark.adb.eni.vswitchId= <your_vswitch_id> \
    --spark-conf spark.adb.eni.securityGroupId= <your_security_group_id>\
    --spark-conf spark.adb.acuPerApp=16\
    --resource-group <your_job_resource_group_name>

Initializing ADB Spark Connector Server
Creating new Spark Connector Server...
Submitting Spark connector server:amv-wz99icf7v3831i7i with config: {"file": "local:///opt/spark/jars/offline-sql.jar", "name": "SparkConnectorServer", "className": "com.aliyun.adb.spark.connectServer.ADBSparkConnectServer", "conf": {"spark.adb.version": "3.5", "spark.adb.uiMeta.enabled": "false", "spark.adb.eni.enabled": "true", "spark.sql.hive.metastore.version": "adb", "spark.adb.eni.vswitchId": "vsw-wz926zcxi9g55ji6or73e", "spark.adb.eni.securityGroupId": "sg-wz909my4jibz0o2wr1kg", "spark.adb.acuPerApp": "16"}}
Submitted Spark connector server ID: s202511101626sz8f1a30a0003023
Waiting for Spark Connect Server to start... s202511101626sz8f1a30a0003023->SUBMITTED
Waiting for Spark Connect Server to start... s202511101626sz8f1a30a0003023->RUNNING
Spark Connect Server started at host: 172.25.219.86
ADB Spark status:RUNNING, AppId:s202511101626sz8f1a30a0003023, Web UI:https://adbsparkui-cn-shenzhen.aliyuncs.c

In [2]:
CREATE DATABASE IF NOT EXISTS db_warehouse;

DataFrame[]

In [ ]:
-- Create a golden layer order summary table. This table will be built based on ADB's datawarehouse storage engine instead of Deltalake for subsecond performance with higher concurrency.
CREATE TABLE IF NOT EXISTS db_warehouse.orders_golden (
    stat_date DATE COMMENT 'Statistics date',
    product_category STRING COMMENT 'Product category',
    order_count BIGINT COMMENT 'Order quantity',
    total_amount DOUBLE COMMENT 'Total transaction volume',
    avg_amount DOUBLE COMMENT 'Average customer spending',
    user_count BIGINT COMMENT 'Number of users',
    peak_hour INT COMMENT 'Peak trading hour',
    peak_hour_order_count BIGINT COMMENT 'Peak hour orders',
    daily_rank_by_amount INT COMMENT 'Rank of category by total amount on the day',
    mom_growth_rate DOUBLE COMMENT 'Month-over-month growth rate of total amount'
)
using adb 
    TBLPROPERTIES (
    'distributeType' = 'HASH',
    'distributeColumns' = 'stat_date',
    'partitionType' = 'value',
    'partitionColumn' = 'stat_date',
    'indexAll' = 'Y',
    'storagePolicy' = 'HOT'
  );   

DataFrame[]

In [ ]:
INSERT OVERWRITE db_warehouse.orders_golden partition(stat_date)
SELECT
s.product_category,
s.order_count AS order_count,
s.total_amount,
s.avg_amount,
s.user_count,
s.peak_hour,
s.peak_hour_order_count,
ROW_NUMBER() OVER (PARTITION BY s.stat_date ORDER BY s.total_amount DESC) AS daily_rank_by_amount,
CASE
WHEN prev_m.total_amount IS NULL OR prev_m.total_amount = 0 THEN NULL
ELSE (s.total_amount - prev_m.total_amount) / prev_m.total_amount
END AS mom_growth_rate,
CAST(s.stat_date AS DATE) AS stat_date
FROM db_lake.orders_silver s
LEFT JOIN (
-- Get same category's total_amount from previous month
SELECT
stat_date,
product_category,
total_amount
FROM db_lake.orders_silver
) prev_m
ON s.product_category = prev_m.product_category
AND ADD_MONTHS(CAST(s.stat_date AS DATE), -1) = CAST(prev_m.stat_date AS DATE);

DataFrame[]